In [1]:
import pandas as pd
import numpy as np

In [2]:
multimedia = pd.read_csv("../deduplication_process/metadata/Zenodo_meta_files/multimedia__(rec_3477891).csv", low_memory=False)
multimedia.info(show_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5683 entries, 0 to 5682
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   coreid      5683 non-null   object 
 1   type        0 non-null      float64
 2   identifier  5683 non-null   object 
 3   license     0 non-null      float64
dtypes: float64(2), object(2)
memory usage: 177.7+ KB


In [3]:
multimedia.head()

coreid  type  \
0  275ad2e7-bc7e-4e74-832e-869825f5bf0b   NaN   
1  cf02ac3a-6204-417c-b342-6f84eab48931   NaN   
2  7be80267-dbe9-4f4b-8f73-c7355447d5e1   NaN   
3  b97011cb-c4fd-4ea9-8828-dc920c7b900a   NaN   
4  6375bf74-3333-4cb6-a0dc-f95c3794edae   NaN   

                                          identifier  license  
0  https://zenodo.org/record/2684906/files/CAM008...      NaN  
1  https://zenodo.org/record/2714333/files/CAM041...      NaN  
2  https://zenodo.org/record/2686762/files/CAM008...      NaN  
3  https://zenodo.org/record/2684906/files/CAM008...      NaN  
4  https://zenodo.org/record/2714333/files/CAM040...      NaN

In [4]:
multimedia.identifier[0]

'https://zenodo.org/record/2684906/files/CAM008538_d.JPG'

Let's get a filename and record number recorded. Would like to add a `zenodo_link` column to see how that matches up to the master file as well. David said these were mostly resolution for records from [3477891](https://zenodo.org/records/3477891) (where these files are from) at download.

`identifier` is non-null for all entries, but there is one non-Zenodo link.

In [5]:
def get_link_filename(identifier):
    if "zenodo" not in identifier:
        link_list = identifier.split("com/")
        link_list[0] = np.nan
    else:
        link_list = identifier.split("/files/")
    # link is first part, filename at end
    return pd.Series(link_list)

def get_record_number(zenodo_link):
    if type(zenodo_link) != float:
        link = zenodo_link.split("record/")
        return link[1]

multimedia[["zenodo_link", "Image_name"]] = multimedia["identifier"].apply(get_link_filename)
multimedia["record_number"] = multimedia["zenodo_link"].apply(get_record_number)
multimedia.head()

coreid  type  \
0  275ad2e7-bc7e-4e74-832e-869825f5bf0b   NaN   
1  cf02ac3a-6204-417c-b342-6f84eab48931   NaN   
2  7be80267-dbe9-4f4b-8f73-c7355447d5e1   NaN   
3  b97011cb-c4fd-4ea9-8828-dc920c7b900a   NaN   
4  6375bf74-3333-4cb6-a0dc-f95c3794edae   NaN   

                                          identifier  license  \
0  https://zenodo.org/record/2684906/files/CAM008...      NaN   
1  https://zenodo.org/record/2714333/files/CAM041...      NaN   
2  https://zenodo.org/record/2686762/files/CAM008...      NaN   
3  https://zenodo.org/record/2684906/files/CAM008...      NaN   
4  https://zenodo.org/record/2714333/files/CAM040...      NaN   

                         zenodo_link       Image_name record_number  
0  https://zenodo.org/record/2684906  CAM008538_d.JPG       2684906  
1  https://zenodo.org/record/2714333  CAM041048_v.JPG       2714333  
2  https://zenodo.org/record/2686762  CAM008842_d.JPG       2686762  
3  https://zenodo.org/record/2684906  CAM008539_v.JPG       2684906  
4  https://zenodo.org/record/2714333  CAM040771_v.JPG       2714333

In [6]:
for link in list(multimedia.identifier):
    if "zenodo" not in link:
        print(link)

http://earthcape-heliconius.s3-eu-west-1.amazonaws.com/F1FD2804C9E643798A7C1B0D9FBDE4AB.JPG


So there is one image that does not have a Zenodo link.

In [7]:
multimedia.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5683 entries, 0 to 5682
Data columns (total 7 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   coreid         5683 non-null   object 
 1   type           0 non-null      float64
 2   identifier     5683 non-null   object 
 3   license        0 non-null      float64
 4   zenodo_link    5682 non-null   object 
 5   Image_name     5683 non-null   object 
 6   record_number  5682 non-null   object 
dtypes: float64(2), object(5)
memory usage: 310.9+ KB


In [8]:
multimedia.nunique()

coreid           2794
type                0
identifier       5683
license             0
zenodo_link        12
Image_name       5683
record_number      12
dtype: int64

The `coreid` is repeated, but the `Image_name` is unique across entries, so this could (hopefully) connect us to the source images.

In [9]:
multimedia.record_number.value_counts()

record_number
2707828    1276
2714333    1113
2686762     986
2684906     863
2677821     703
2702457     276
2682458     158
2682669     124
2552371      91
2550097      50
2553977      22
2813153      20
Name: count, dtype: int64

Interesting, it would seem that record 3477891 is a collection of these 12 other records. It matches with this [GBIF Collection](https://www.gbif.org/dataset/34f8683a-dfc0-46b8-acf6-390fe5ca6b92) that is the "collection records from the research group of Chris Jiggins at the University of Cambridge derived from almost 20 years of field studies. Many records include images as well as locality data." released in October 2019.

In [10]:
occurrence = pd.read_csv("../deduplication_process/metadata/Zenodo_meta_files/occurrences__(rec_3477891).csv",low_memory=False)
occurrence.info(show_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4372 entries, 0 to 4371
Data columns (total 29 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   id                             4372 non-null   object 
 1   occurrenceID                   4372 non-null   object 
 2   catalogNumber                  4372 non-null   object 
 3   datasetName                    4372 non-null   object 
 4   recordNumber                   0 non-null      float64
 5   otherCatalogNumbers            33 non-null     object 
 6   basisOfRecord                  4372 non-null   object 
 7   eventDate                      3806 non-null   object 
 8   locality                       4372 non-null   object 
 9   country                        4372 non-null   object 
 10  decimalLatitude                4372 non-null   float64
 11  decimalLongitude               4372 non-null   float64
 12  geodeticDatum                  4372 non-null   i

In [11]:
occurrence[(occurrence.columns)[:4]].nunique()

id               4372
occurrenceID     4372
catalogNumber    4372
datasetName         1
dtype: int64

Are `id` and `occurrenceID` all equal?

In [12]:
occurrence.loc[occurrence["id"] == occurrence["occurrenceID"]].shape

(4372, 29)

This has a record number column, but there are no non-null values, so we'll try to fill that in. Except there is nothing to use to fill it in...we have to connect on `catalogNumber` to the `id` to the `coreid`, but `catalogNumber` is just the CAMID and we have more unique IDs than there are in the multimedia file...

In [13]:
occurrence.head()

id                          occurrenceID  \
0  00075b7f-3920-4987-a3e4-e98568a38558  00075b7f-3920-4987-a3e4-e98568a38558   
1  000dc8ca-5d60-4aff-9823-33d20d52c7cd  000dc8ca-5d60-4aff-9823-33d20d52c7cd   
2  001b4619-bfe3-4a89-9709-45a70c1fa380  001b4619-bfe3-4a89-9709-45a70c1fa380   
3  0021e86f-64b3-4ce8-b872-f783f00f5f6a  0021e86f-64b3-4ce8-b872-f783f00f5f6a   
4  0034a857-9ed6-45be-b437-8e20eef541bb  0034a857-9ed6-45be-b437-8e20eef541bb   

  catalogNumber                                        datasetName  \
0     CAM040599  Heliconiine Butterfly Collection Records from ...   
1     CAM040277  Heliconiine Butterfly Collection Records from ...   
2     CAM120368  Heliconiine Butterfly Collection Records from ...   
3     CAM014638  Heliconiine Butterfly Collection Records from ...   
4     CAM008071  Heliconiine Butterfly Collection Records from ...   

   recordNumber otherCatalogNumbers      basisOfRecord   eventDate  \
0           NaN                 NaN  PreservedSpecimen  2017-03-07   
1           NaN                 NaN  PreservedSpecimen  2017-01-30   
2           NaN                 NaN  PreservedSpecimen  2005-11-15   
3           NaN                 NaN  PreservedSpecimen  2009-11-23   
4           NaN                 NaN  PreservedSpecimen  2000-12-17   

                     locality  country  ...  \
0        Mashpi to Pachijal 2  Ecuador  ...   
1   Km 119 Baeza - Lago Agrio  Ecuador  ...   
2  Anangu Boca del Rio ECD OR  Ecuador  ...   
3                 Puerta Lara   Panamá  ...   
4                 Gamboa #183   Panamá  ...   

                        scientificName  scientificNameAuthorship   taxonRank  \
0        Heliconius cydno ssp. alithea                       NaN  Subspecies   
1                         Actinote sp.                       NaN     Species   
2        Pseudoscada timna ssp. utilla                       NaN  Subspecies   
3  Heliconius melpomene ssp. melpomene                       NaN  Subspecies   
4                  Anthanassa drusilla                       NaN     Species   

         genus       family        order    class   kingdom  \
0   Heliconius  Nymphalidae  Lepidoptera  Insecta  Animalia   
1     Actinote  Nymphalidae  Lepidoptera  Insecta  Animalia   
2  Pseudoscada  Nymphalidae  Lepidoptera  Insecta  Animalia   
3   Heliconius  Nymphalidae  Lepidoptera  Insecta  Animalia   
4   Anthanassa  Nymphalidae  Lepidoptera  Insecta  Animalia   

   coordinateUncertaintyInMeters dynamicProperties  
0                            NaN                {}  
1                            NaN                {}  
2                            NaN                {}  
3                            NaN                {}  
4                            NaN                {}  

[5 rows x 29 columns]

How many unique CAMIDs do we have in `multimedia`?

In [14]:
def get_camid(image_name):
    if "_" in image_name:
        return image_name.split("_")[0]
    else:
        # We have at least one record with image name that doesn't have CAMID (the non-zenodo record)
        return np.nan

multimedia["CAMID"] = multimedia["Image_name"].apply(get_camid)
multimedia["CAMID"].nunique()

2802

Okay, so there are more unique `CAMID`s than there are unique `coreid`s, but less than there are unique CAMIDs (`catalogNumber`) in `occurrence`...

What do I get if I merge these on `CAMID` and `coreid`?

In [15]:
test_merge = pd.merge(multimedia,
                      occurrence,
                      left_on = ["coreid", "CAMID"],
                      right_on = ["id", "catalogNumber"],
                      how = "inner")
test_merge.info(show_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5407 entries, 0 to 5406
Data columns (total 37 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   coreid                         5407 non-null   object 
 1   type                           0 non-null      float64
 2   identifier                     5407 non-null   object 
 3   license                        0 non-null      float64
 4   zenodo_link                    5407 non-null   object 
 5   Image_name                     5407 non-null   object 
 6   record_number                  5407 non-null   object 
 7   CAMID                          5407 non-null   object 
 8   id                             5407 non-null   object 
 9   occurrenceID                   5407 non-null   object 
 10  catalogNumber                  5407 non-null   object 
 11  datasetName                    5407 non-null   object 
 12  recordNumber                   0 non-null      f

So there are about 270 images listed in `multimedia` that are unaccounted for in `occurences`.

In [16]:
test_merge[list(test_merge.columns)[:12]].head()

coreid  type  \
0  275ad2e7-bc7e-4e74-832e-869825f5bf0b   NaN   
1  275ad2e7-bc7e-4e74-832e-869825f5bf0b   NaN   
2  cf02ac3a-6204-417c-b342-6f84eab48931   NaN   
3  cf02ac3a-6204-417c-b342-6f84eab48931   NaN   
4  7be80267-dbe9-4f4b-8f73-c7355447d5e1   NaN   

                                          identifier  license  \
0  https://zenodo.org/record/2684906/files/CAM008...      NaN   
1  https://zenodo.org/record/2684906/files/CAM008...      NaN   
2  https://zenodo.org/record/2714333/files/CAM041...      NaN   
3  https://zenodo.org/record/2714333/files/CAM041...      NaN   
4  https://zenodo.org/record/2686762/files/CAM008...      NaN   

                         zenodo_link       Image_name record_number  \
0  https://zenodo.org/record/2684906  CAM008538_d.JPG       2684906   
1  https://zenodo.org/record/2684906  CAM008538_v.JPG       2684906   
2  https://zenodo.org/record/2714333  CAM041048_v.JPG       2714333   
3  https://zenodo.org/record/2714333  CAM041048_d.JPG       2714333   
4  https://zenodo.org/record/2686762  CAM008842_d.JPG       2686762   

       CAMID                                    id  \
0  CAM008538  275ad2e7-bc7e-4e74-832e-869825f5bf0b   
1  CAM008538  275ad2e7-bc7e-4e74-832e-869825f5bf0b   
2  CAM041048  cf02ac3a-6204-417c-b342-6f84eab48931   
3  CAM041048  cf02ac3a-6204-417c-b342-6f84eab48931   
4  CAM008842  7be80267-dbe9-4f4b-8f73-c7355447d5e1   

                           occurrenceID catalogNumber  \
0  275ad2e7-bc7e-4e74-832e-869825f5bf0b     CAM008538   
1  275ad2e7-bc7e-4e74-832e-869825f5bf0b     CAM008538   
2  cf02ac3a-6204-417c-b342-6f84eab48931     CAM041048   
3  cf02ac3a-6204-417c-b342-6f84eab48931     CAM041048   
4  7be80267-dbe9-4f4b-8f73-c7355447d5e1     CAM008842   

                                         datasetName  
0  Heliconiine Butterfly Collection Records from ...  
1  Heliconiine Butterfly Collection Records from ...  
2  Heliconiine Butterfly Collection Records from ...  
3  Heliconiine Butterfly Collection Records from ...  
4  Heliconiine Butterfly Collection Records from ...

In [17]:
test_merge[["coreid", "CAMID", "identifier", "record_number"]].nunique()

coreid           2713
CAMID            2713
identifier       5407
record_number      10
dtype: int64

Uniqueness counts from `multimedia`:
```
CAMID            2802
coreid           2794
identifier       5683
Image_name       5683
record_number      12
```
It seems there are 2 records that don't match on IDs, which is a loss of 81 unique listings in `multimedia`.

How will this compare to the entries from record 3477891 in our master file? Also, are these other records in there?

In [18]:
df = pd.read_csv("../Jiggins_Zenodo_Img_Master.csv", low_memory = False)

odd_record = df.loc[df["record_number"] == 3477891]
odd_record.info()

<class 'pandas.core.frame.DataFrame'>
Index: 5501 entries, 3235 to 42852
Data columns (total 28 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             5501 non-null   object
 1   X                 5501 non-null   int64 
 2   Image_name        5501 non-null   object
 3   View              5501 non-null   object
 4   zenodo_name       5501 non-null   object
 5   zenodo_link       5501 non-null   object
 6   Sequence          5501 non-null   object
 7   Taxonomic_Name    5501 non-null   object
 8   Locality          5501 non-null   object
 9   Sample_accession  925 non-null    object
 10  Collected_by      0 non-null      object
 11  Other_ID          12 non-null     object
 12  Date              5025 non-null   object
 13  Dataset           5501 non-null   object
 14  Store             5421 non-null   object
 15  Brood             4 non-null      object
 16  Death_Date        0 non-null      object
 17  Cross_Type     

In [19]:
id_cols = ["CAMID", "X", "Image_name", "zenodo_name", "zenodo_link", "file_url", "Dataset"]

In [20]:
odd_record[id_cols].nunique()

CAMID          2704
X              5501
Image_name     5497
zenodo_name       1
zenodo_link       1
file_url       5497
Dataset           1
dtype: int64

This falls somewhere between the `multimedia` & `occurrence` merge, and the `multimedia` file. Let's see a sample of these images then try aligning it with `multimedia` on `Image_name`.

In [21]:
odd_record[id_cols].head()

CAMID      X       Image_name                    zenodo_name  \
3235  CAM000001  44387  CAM000001_v.JPG  occurences_and_multimedia.csv   
3236  CAM000001  44386  CAM000001_d.JPG  occurences_and_multimedia.csv   
3237  CAM000003  44388  CAM000003_d.JPG  occurences_and_multimedia.csv   
3240  CAM000003  44389  CAM000003_v.JPG  occurences_and_multimedia.csv   
3242  CAM000004  44390  CAM000004_d.JPG  occurences_and_multimedia.csv   

                            zenodo_link  \
3235  https://zenodo.org/record/3477891   
3236  https://zenodo.org/record/3477891   
3237  https://zenodo.org/record/3477891   
3240  https://zenodo.org/record/3477891   
3242  https://zenodo.org/record/3477891   

                                               file_url  \
3235  https://zenodo.org/record/3477891/files/CAM000...   
3236  https://zenodo.org/record/3477891/files/CAM000...   
3237  https://zenodo.org/record/3477891/files/CAM000...   
3240  https://zenodo.org/record/3477891/files/CAM000...   
3242  https://zenodo.org/record/3477891/files/CAM000...   

                                                Dataset  
3235  Heliconiine Butterfly Collection Records from ...  
3236  Heliconiine Butterfly Collection Records from ...  
3237  Heliconiine Butterfly Collection Records from ...  
3240  Heliconiine Butterfly Collection Records from ...  
3242  Heliconiine Butterfly Collection Records from ...

They are all labeled as that dataset with the `zenodo_name` "occurrences_and_multimedia.csv" because it was a combo of these used by Christopher to populate the CSV.

In [22]:
odd_multimedia = pd.merge(odd_record[id_cols],
                          multimedia,
                          on = "Image_name",
                          how = "inner",
                          suffixes = ("_master", "_media"))
odd_multimedia.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5501 entries, 0 to 5500
Data columns (total 14 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   CAMID_master        5501 non-null   object 
 1   X                   5501 non-null   int64  
 2   Image_name          5501 non-null   object 
 3   zenodo_name         5501 non-null   object 
 4   zenodo_link_master  5501 non-null   object 
 5   file_url            5501 non-null   object 
 6   Dataset             5501 non-null   object 
 7   coreid              5501 non-null   object 
 8   type                0 non-null      float64
 9   identifier          5501 non-null   object 
 10  license             0 non-null      float64
 11  zenodo_link_media   5501 non-null   object 
 12  record_number       5501 non-null   object 
 13  CAMID_media         5409 non-null   object 
dtypes: float64(2), int64(1), object(11)
memory usage: 601.8+ KB


In [23]:
odd_multimedia.nunique()

CAMID_master          2704
X                     5501
Image_name            5497
zenodo_name              1
zenodo_link_master       1
file_url              5497
Dataset                  1
coreid                2704
type                     0
identifier            5497
license                  0
zenodo_link_media       12
record_number           12
CAMID_media           2712
dtype: int64

Looks like all the images were captured (there are more entries than unique `Image_name` & URL), so we should be able to replace the URLs in the master file with the multimedia image URLs directly.

We do want to compare record numbers to the master file first.

In [24]:
media_records = list(multimedia.record_number.unique())
media_imgs = list(multimedia.Image_name.unique())
master_records = list(df.record_number.unique())

overlap_records = [record for record in media_records if record in master_records]
len(overlap_records)

0

Ahhh no duplication then. Interesting (and good!)

In [25]:
non_odd_df = df.loc[df["record_number"] != 3477891]

test_odd_merge = pd.merge(odd_record,
                          non_odd_df,
                          on = "Image_name",
                          how = "inner")
test_odd_merge.shape

(5501, 55)

In [26]:
multimedia.loc[multimedia["Image_name"] == "CAM000003_v.JPG", "identifier"].values[0]

'https://zenodo.org/record/2677821/files/CAM000003_v.JPG'

Duplication in `Image_name`, though that's not necessarily unexpected.

In [27]:
for image_name in list(odd_record.Image_name.unique()):
    url = multimedia.loc[multimedia["Image_name"] == image_name, "identifier"].values[0]
    df.loc[(df["record_number"] == 3477891) & (df["Image_name"] == image_name), "file_url"] = url

df.loc[df["record_number"] == 3477891].nunique()

CAMID               2704
X                   5501
Image_name          5497
View                   2
zenodo_name            1
zenodo_link            1
Sequence            2704
Taxonomic_Name       195
Locality             205
Sample_accession     446
Collected_by           0
Other_ID               5
Date                 200
Dataset                1
Store                 55
Brood                  2
Death_Date             0
Cross_Type             0
Stage                  0
Sex                    3
Unit_Type              2
file_type              1
record_number          1
species              121
subspecies            93
genus                 38
file_url            5497
hybrid_stat            2
dtype: int64

In [28]:
df[id_cols].nunique()

CAMID          11991
X              44809
Image_name     36281
zenodo_name       33
zenodo_link       30
file_url       39297
Dataset            8
dtype: int64

In [29]:
df.Dataset.value_counts()

Dataset
Heliconiine Butterfly Collection Records from University of Cambridge    25211
Patricio Salazar                                                          7519
Nadeau Sheffield                                                          3233
Bogota Collection (Camilo Salazar)                                         982
Cambridge Collection                                                        47
Mallet                                                                      22
Merril_Gamboa                                                                6
STRI Collection (Owen)                                                       4
Name: count, dtype: int64

In [30]:
HBCRUC = "Heliconiine Butterfly Collection Records from University of Cambridge"
df.loc[df.Dataset == HBCRUC].nunique()

CAMID                6538
X                   25211
Image_name          17362
View                    7
zenodo_name            17
zenodo_link            17
Sequence             6538
Taxonomic_Name        287
Locality              372
Sample_accession      485
Collected_by            0
Other_ID             1123
Date                  282
Dataset                 1
Store                 102
Brood                 102
Death_Date              0
Cross_Type              0
Stage                   0
Sex                     3
Unit_Type               2
file_type               2
record_number          17
species               207
subspecies             99
genus                  82
file_url            19710
hybrid_stat             2
dtype: int64

In [31]:
df.to_csv("../deduplication_process/Jiggins_Zenodo_Img_Master_3477891Patch.csv", index = False)